In [1]:
import pandas as pd
import numpy as np
import torch
import sys
sys.path.append("../")
from datasets import *
from trainer import *
from model_builder import build_model
from visualize import visualize_graph_from_edges

/Users/bytedance/Documents/project/DeepEST_Complex/DeepEST/models/../trainer/trainer.py:10: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import trange


In [2]:
df = pd.read_csv('../Data/date_range.pkl', encoding="ISO-8859-1")
temp_list = df.iloc[0:10, 0].values.tolist()
date_list = [date[0:10] for date in temp_list]
date_list

['2020-08-01',
 '2020-08-02',
 '2020-08-03',
 '2020-08-04',
 '2020-08-05',
 '2020-08-06',
 '2020-08-07',
 '2020-08-08',
 '2020-08-09',
 '2020-08-10']

In [3]:
x_list = []

In [4]:
claim_data = torch.Tensor(pd.read_pickle('../data/claim_tensor.pkl'))
county_data = torch.Tensor(pd.read_pickle('../data/county_tensor.pkl'))
hospitalizations_data = torch.Tensor(pd.read_pickle('../data/hospitalizations.pkl'))
distance_matrix = torch.Tensor(pd.read_pickle('../data/distance_mat.pkl'))
data_time = pd.read_pickle('../data/date_range.pkl') #这个是list
claim_data.shape, county_data.shape, hospitalizations_data.shape, distance_matrix.shape,
dynamic_data = torch.cat((claim_data,torch.unsqueeze(hospitalizations_data, -1)), -1)
static_data = county_data
label = torch.unsqueeze(hospitalizations_data, -1)
dynamic_data = dynamic_data[:10]
static_data = static_data[:10]
label = label[:10]

In [5]:
st_preprocess = preprocess_data(dynamic_data = dynamic_data, static_data = static_data, label = label, input_window = 7, output_window = 3, type= 'spatial-temporal')
t_preprocess = preprocess_data(dynamic_data = dynamic_data, static_data = static_data, label = label, input_window = 7, output_window = 3, type= 'temporal', mode=0, method="mean")

In [6]:
threshold = 50000
edge_index =  construct_adjacency_matrix(static_data, threshold)

In [7]:
visualize_graph_from_edges(edge_index)

In [8]:
trainset, valset, testset = st_preprocess.get_dl_dataset()
train_st_loader, val_st_loader, test_st_loader = get_dataloader(trainset, 8, True), get_dataloader(valset, 8, False), get_dataloader(testset, 8, False)

In [9]:
trainset, valset, testset = st_preprocess.get_dl_dataset()
train_st_loader, val_st_loader, test_st_loader = get_dataloader(trainset, 8, True), get_dataloader(valset, 8, False), get_dataloader(testset, 8, False)

In [10]:
model = build_model(preprocess=st_preprocess, model_name="taprsv", edge_index=edge_index)
trainer = dl_trainer(model= model)
trainer.train(train_dataloader= train_st_loader, val_dataloader= val_st_loader, epochs= 10)


Epoch 0 / 10:   0%|          | 0/47 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

---------------Save Best Checkpoint---------------
update min_loss, loss is 0.36860764026641846
mean_loss is 0.8764778971672058


Epoch 1 / 10:   0%|          | 0/47 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

...

  0%|          | 0/15 [00:00<?, ?it/s]

mean_loss is 0.2886075973510742


Epoch 9 / 10:   0%|          | 0/47 [00:00<?, ?it/s]

  0%|          | 0/15 [00:00<?, ?it/s]

mean_loss is 0.28667256236076355


In [11]:
tester = dl_tester(model=model)
tester.test(test_st_loader, preprocess= st_preprocess)

  0%|          | 0/15 [00:00<?, ?it/s]

y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape is torch.Size([8, 10, 3])
y_true.shape is torch.Size([8, 10, 3]), y_pred.shape

In [12]:
trainset, valset, testset = t_preprocess.get_ml_dataset()
train_t_loader, val_t_loader, test_t_loader  = get_dataloader(trainset, 8, True), get_dataloader(valset, 8, False), get_dataloader(testset, 8, False)
model = build_model(preprocess=t_preprocess, model_name="xgboost")
trainer = ml_trainer(model= model)
trainer.train(train_dataloader= train_t_loader)
print('111')
trainer.evaluate(val_dataloader=val_t_loader)

x.shape is torch.Size([374, 245]), y.shape is (374, 3)


In [ ]:
trainset, valset, testset = t_preprocess.get_ml_dataset_without_divide()
train_t_loader, val_t_loader, test_t_loader = get_dataloader(trainset, 8, True), get_dataloader(valset, 8, False), get_dataloader(testset, 8, False)
model = build_model(preprocess=t_preprocess, model_name="arima")
trainer = ml_trainer(model= model)
trainer.train(train_dataloader= train_t_loader)
trainer.evaluate(val_dataloader=val_t_loader)

In [ ]:
trainset, valset, testset = t_preprocess.get_ml_dataset_without_divide()
train_t_loader, val_t_loader, test_t_loader = get_dataloader(trainset, 8, True), get_dataloader(valset, 8, False), get_dataloader(testset, 8, False)
model = build_model(preprocess=t_preprocess, model_name="sir", S0 = 500000, I0 = 60, R0 = 0)
trainer = ml_trainer(model= model)
trainer.train(train_dataloader= train_t_loader)
trainer.evaluate(val_dataloader= val_t_loader)

In [ ]:
trainset, valset, testset = t_preprocess.get_ml_dataset_without_divide()
train_t_loader, val_t_loader, test_t_loader= get_dataloader(trainset, 8, True), get_dataloader(valset, 8, False), get_dataloader(testset, 8, False)
model = build_model(preprocess=t_preprocess, model_name="seir", S0 = 10000000, E0 = 800, I0 = 60, R0 = 0)
trainer = ml_trainer(model= model)
trainer.train(train_dataloader= train_t_loader)
trainer.evaluate(val_dataloader=val_t_loader)

In [ ]:
trainset, valset, testset = t_preprocess.get_dl_dataset()
train_temporal_loader, val_temporal_loader, test_temporal_loader = get_dataloader(trainset, 8, True), get_dataloader(valset, 8, False), get_dataloader(testset, 8, False)
model = build_model(preprocess=t_preprocess, model_name="lstm", edge_index=edge_index)
trainer = dl_trainer(model= model)
trainer.train(train_dataloader= train_temporal_loader, val_dataloader= val_temporal_loader, epochs= 10)
tester = dl_tester(model=model)
tester.test(test_dataloader=test_temporal_loader)